In [149]:
import pandas as pd
import numpy as np
import plotly.express as xpx

# Test SVM Regression on this data

In [164]:
air = pd.read_csv('air.csv', delimiter=';')

In [165]:
air.head()

Date      Time CO(GT)  NMHC(GT) C6H6(GT)  NOx(GT)  NO2(GT)     T  \
0  11/03/2004  00.00.00    1,2        31      3,6       62       77  11,3   
1  11/03/2004  01.00.00      1        31      3,3       62       76  10,7   
2  11/03/2004  02.00.00    0,9        24      2,3       45       60  10,7   
3  11/03/2004  03.00.00    0,6        19      1,7     -200     -200  10,3   
4  11/03/2004  04.00.00   -200        14      1,3       21       34  10,1   

     RH      AH  
0  56,8  0,7603  
1  60,0  0,7702  
2  59,7  0,7648  
3  60,2  0,7517  
4  60,5  0,7465

In [166]:
air = air.replace(to_replace=r',', value='.', regex=True)
print(air.info())
air.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9336 entries, 0 to 9335
Data columns (total 10 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   Date      9336 non-null   object
 1   Time      9336 non-null   object
 2   CO(GT)    9336 non-null   object
 3   NMHC(GT)  9336 non-null   int64 
 4   C6H6(GT)  9336 non-null   object
 5   NOx(GT)   9336 non-null   int64 
 6   NO2(GT)   9336 non-null   int64 
 7   T         9336 non-null   object
 8   RH        9336 non-null   object
 9   AH        9336 non-null   object
dtypes: int64(3), object(7)
memory usage: 729.5+ KB
None


Date      Time CO(GT)  NMHC(GT) C6H6(GT)  NOx(GT)  NO2(GT)     T  \
0  11/03/2004  00.00.00    1.2        31      3.6       62       77  11.3   
1  11/03/2004  01.00.00      1        31      3.3       62       76  10.7   
2  11/03/2004  02.00.00    0.9        24      2.3       45       60  10.7   
3  11/03/2004  03.00.00    0.6        19      1.7     -200     -200  10.3   
4  11/03/2004  04.00.00   -200        14      1.3       21       34  10.1   

     RH      AH  
0  56.8  0.7603  
1  60.0  0.7702  
2  59.7  0.7648  
3  60.2  0.7517  
4  60.5  0.7465

Change Date and Time format.

In [167]:
import datetime
def change_date(date):
    return datetime.datetime.strptime(date, '%d/%m/%Y').strftime('%Y-%m-%d')

def change_time(time):
    return datetime.datetime.strptime(time, "%H.%M.%S").strftime('%H:%M:%S')

In [168]:
air['Date'] = air['Date'].apply(change_date)
air['Time'] = air['Time'].apply(change_time)

In [169]:
air['ts'] = pd.to_datetime(air['Date'] + ' ' + air['Time'])

In [170]:
air.set_index('ts', inplace=True)
air.drop(['Date', 'Time'], axis=1, inplace=True)

In [171]:
air.head(3)

CO(GT)  NMHC(GT) C6H6(GT)  NOx(GT)  NO2(GT)     T    RH  \
ts                                                                            
2004-03-11 00:00:00    1.2        31      3.6       62       77  11.3  56.8   
2004-03-11 01:00:00      1        31      3.3       62       76  10.7  60.0   
2004-03-11 02:00:00    0.9        24      2.3       45       60  10.7  59.7   

                         AH  
ts                           
2004-03-11 00:00:00  0.7603  
2004-03-11 01:00:00  0.7702  
2004-03-11 02:00:00  0.7648

In [172]:
# Plot 
fig = px.line()

# Only thing I figured is - I could do this 
fig.add_scatter(x=air.index, y=air['RH'], mode='lines', name='CO(GT)')
fig.add_scatter(x=air.index, y=air['T'], mode='lines', name='C6H6(GT)')

# Show plot 
fig.show();

In [173]:
px.scatter_matrix(air)

Replace outliers through interpolation.

In [174]:
air[['CO(GT)', 'C6H6(GT)', 'T', 'RH','AH']] = air[['CO(GT)', 'C6H6(GT)', 'T', 'RH','AH']].astype(float)

In [175]:
print(air.columns)
air.info()

Index(['CO(GT)', 'NMHC(GT)', 'C6H6(GT)', 'NOx(GT)', 'NO2(GT)', 'T', 'RH',
       'AH'],
      dtype='object')
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 9336 entries, 2004-03-11 00:00:00 to 2005-04-03 23:00:00
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   CO(GT)    9336 non-null   float64
 1   NMHC(GT)  9336 non-null   int64  
 2   C6H6(GT)  9336 non-null   float64
 3   NOx(GT)   9336 non-null   int64  
 4   NO2(GT)   9336 non-null   int64  
 5   T         9336 non-null   float64
 6   RH        9336 non-null   float64
 7   AH        9336 non-null   float64
dtypes: float64(5), int64(3)
memory usage: 656.4 KB


In [176]:
air['RH'].value_counts()

-200.0    366
 53.1      31
 47.8      30
 57.9      30
 60.8      27
         ... 
 17.6       1
 12.9       1
 12.2       1
 11.6       1
 88.7       1
Name: RH, Length: 754, dtype: int64

In [177]:
# Yields a tuple of column name and series for each column in the dataframe
for col in air.iteritems():
    air[col[0]] = col[1].replace(-200,col[1].mean())

In [178]:
air['RH'].value_counts()

39.470169    366
53.100000     31
47.800000     30
57.900000     30
60.800000     27
            ... 
88.700000      1
85.600000      1
9.300000       1
84.600000      1
12.200000      1
Name: RH, Length: 754, dtype: int64

In [179]:
# Plot 
fig = px.line()

# Only thing I figured is - I could do this 
fig.add_scatter(x=air.index, y=air['RH'], mode='lines', name='CO(GT)')
fig.add_scatter(x=air.index, y=air['T'], mode='lines', name='C6H6(GT)')

# Show plot 
fig.show();

In [180]:
air.describe()

CO(GT)     NMHC(GT)     C6H6(GT)      NOx(GT)      NO2(GT)  \
count  9336.000000  9336.000000  9336.000000  9336.000000  9336.000000   
mean     -4.408581  -122.334251     9.764067   233.179024   103.392728   
std      14.059723   129.152863     7.478223   195.755089    48.657174   
min     -34.267427  -159.182198     0.100000     2.000000     2.000000   
25%       0.600000  -159.182198     4.000000   112.000000    58.013710   
50%       1.500000  -159.182198     7.900000   168.488325    96.000000   
75%       2.600000  -159.182198    13.600000   284.000000   133.000000   
max      11.900000  1189.000000    63.700000  1479.000000   340.000000   

                 T           RH           AH  
count  9336.000000  9336.000000  9336.000000  
mean     17.988765    48.858139     0.717254  
std       8.819209    17.081294     1.580015  
min      -1.900000     9.200000    -6.854640  
25%      10.900000    36.600000     0.691600  
50%      17.200000    48.500000     0.978500  
75%      24.100000    61.900000     1.298025  
max      44.600000    88.700000     2.231000

In [181]:
air.columns

Index(['CO(GT)', 'NMHC(GT)', 'C6H6(GT)', 'NOx(GT)', 'NO2(GT)', 'T', 'RH',
       'AH'],
      dtype='object')

# Predict values (Regression)

We will use the variables `'NMHC(GT)', 'C6H6(GT)', 'NOx(GT)', 'NO2(GT)', 'T', 'RH','AH'` to predict the variable `CO(GT)`.

For training we will use all of the 2004 data and than predict the values for 2005. Note that the data starts at the *2004-03-11 00:00:00* and ends *2005-04-03 23:00:00*. Therefore roughly 7 months trainings data and 4 months predicting.

In [19]:
X = air[['NMHC(GT)', 'C6H6(GT)', 'NOx(GT)', 'NO2(GT)', 'T', 'RH', 'AH']]
y = air['CO(GT)']
# y_index = air['CO(GT)'].index

In [20]:
print(X.shape)
print(y.shape)

(9336, 7)
(9336,)


In [21]:
air.index

DatetimeIndex(['2004-03-11 00:00:00', '2004-03-11 01:00:00',
               '2004-03-11 02:00:00', '2004-03-11 03:00:00',
               '2004-03-11 04:00:00', '2004-03-11 05:00:00',
               '2004-03-11 06:00:00', '2004-03-11 07:00:00',
               '2004-03-11 08:00:00', '2004-03-11 09:00:00',
               ...
               '2005-04-03 14:00:00', '2005-04-03 15:00:00',
               '2005-04-03 16:00:00', '2005-04-03 17:00:00',
               '2005-04-03 18:00:00', '2005-04-03 19:00:00',
               '2005-04-03 20:00:00', '2005-04-03 21:00:00',
               '2005-04-03 22:00:00', '2005-04-03 23:00:00'],
              dtype='datetime64[ns]', name='ts', length=9336, freq=None)

In [22]:
start = '2004-03-11 00:00:00'
stop = '2004-12-31 23:00:00'

X_train = X.iloc[X.index <= stop].values
X_test = X.iloc[X.index > stop].values

y_train = y.iloc[y.index <= stop].values
y_test = y.iloc[y.index > stop].values

test_dates = y.iloc[y.index > stop].index

In [23]:
from sklearn import svm
clf_baseline = svm.SVR(C=10.0, epsilon=0.2)
clf_baseline.fit(X_train, y_train)
preds_baseline = clf_baseline.predict(X_test)

SVR(C=10.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.2, gamma='scale',
    kernel='rbf', max_iter=-1, shrinking=True, tol=0.001, verbose=False)

In [24]:
# Plot 
fig = px.line()

# Only thing I figured is - I could do this 
fig.add_scatter(x=test_dates, y=y_test, mode='lines', name='Real Values CO(GT)')
fig.add_scatter(x=test_dates, y=preds_baseline, mode='lines', name='Predictions CO(GT)')

# Show plot 
fig.show();

In [25]:
from sklearn.metrics import mean_absolute_error
print('MAE for the baseline is: {}'.format(mean_absolute_error(y_test, preds_baseline)))

MAE for the baseline is: 4.987846899451455


### Parameter tuning

In [56]:
from sklearn.model_selection import GridSearchCV

parameters = {'kernel':['rbf'],
              'C':[0.01, 0.1, 3, 5, 10, 15, 30],
              'epsilon':[0.01, 0.1, 3, 10, 15, 30]}

In [57]:
svr_gs = svm.SVR()
clf_gs = GridSearchCV(svr_gs, parameters, verbose=2)
clf_gs.fit(X_train, y_train)

Fitting 5 folds for each of 42 candidates, totalling 210 fits
[CV] C=0.01, epsilon=0.01, kernel=rbf ................................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] ................. C=0.01, epsilon=0.01, kernel=rbf, total=   0.9s
[CV] C=0.01, epsilon=0.01, kernel=rbf ................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.9s remaining:    0.0s


[CV] ................. C=0.01, epsilon=0.01, kernel=rbf, total=   0.9s
[CV] C=0.01, epsilon=0.01, kernel=rbf ................................
[CV] ................. C=0.01, epsilon=0.01, kernel=rbf, total=   0.9s
[CV] C=0.01, epsilon=0.01, kernel=rbf ................................
[CV] ................. C=0.01, epsilon=0.01, kernel=rbf, total=   0.9s
[CV] C=0.01, epsilon=0.01, kernel=rbf ................................
[CV] ................. C=0.01, epsilon=0.01, kernel=rbf, total=   0.9s
[CV] C=0.01, epsilon=0.1, kernel=rbf .................................
[CV] .................. C=0.01, epsilon=0.1, kernel=rbf, total=   0.8s
[CV] C=0.01, epsilon=0.1, kernel=rbf .................................
[CV] .................. C=0.01, epsilon=0.1, kernel=rbf, total=   0.8s
[CV] C=0.01, epsilon=0.1, kernel=rbf .................................
[CV] .................. C=0.01, epsilon=0.1, kernel=rbf, total=   0.8s
[CV] C=0.01, epsilon=0.1, kernel=rbf .................................
[CV] .

[CV] .................... C=3, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=3, epsilon=0.01, kernel=rbf ...................................
[CV] .................... C=3, epsilon=0.01, kernel=rbf, total=   1.0s
[CV] C=3, epsilon=0.01, kernel=rbf ...................................
[CV] .................... C=3, epsilon=0.01, kernel=rbf, total=   1.0s
[CV] C=3, epsilon=0.01, kernel=rbf ...................................
[CV] .................... C=3, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=3, epsilon=0.01, kernel=rbf ...................................
[CV] .................... C=3, epsilon=0.01, kernel=rbf, total=   1.0s
[CV] C=3, epsilon=0.1, kernel=rbf ....................................
[CV] ..................... C=3, epsilon=0.1, kernel=rbf, total=   1.0s
[CV] C=3, epsilon=0.1, kernel=rbf ....................................
[CV] ..................... C=3, epsilon=0.1, kernel=rbf, total=   1.0s
[CV] C=3, epsilon=0.1, kernel=rbf ....................................
[CV] .

[CV] ................... C=10, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=10, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=10, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=10, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=10, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=10, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=10, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=10, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=10, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=10, epsilon=0.1, kernel=rbf ...................................
[CV] .................... C=10, epsilon=0.1, kernel=rbf, total=   1.0s
[CV] C=10, epsilon=0.1, kernel=rbf ...................................
[CV] .................... C=10, epsilon=0.1, kernel=rbf, total=   1.0s
[CV] C=10, epsilon=0.1, kernel=rbf ...................................
[CV] .

[CV] ................... C=30, epsilon=0.01, kernel=rbf, total=   1.0s
[CV] C=30, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=30, epsilon=0.01, kernel=rbf, total=   1.0s
[CV] C=30, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=30, epsilon=0.01, kernel=rbf, total=   1.0s
[CV] C=30, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=30, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=30, epsilon=0.01, kernel=rbf ..................................
[CV] ................... C=30, epsilon=0.01, kernel=rbf, total=   1.1s
[CV] C=30, epsilon=0.1, kernel=rbf ...................................
[CV] .................... C=30, epsilon=0.1, kernel=rbf, total=   1.1s
[CV] C=30, epsilon=0.1, kernel=rbf ...................................
[CV] .................... C=30, epsilon=0.1, kernel=rbf, total=   1.2s
[CV] C=30, epsilon=0.1, kernel=rbf ...................................
[CV] .

[Parallel(n_jobs=1)]: Done 210 out of 210 | elapsed:  1.9min finished


GridSearchCV(cv=None, error_score=nan,
             estimator=SVR(C=1.0, cache_size=200, coef0=0.0, degree=3,
                           epsilon=0.1, gamma='scale', kernel='rbf',
                           max_iter=-1, shrinking=True, tol=0.001,
                           verbose=False),
             iid='deprecated', n_jobs=None,
             param_grid={'C': [0.01, 0.1, 3, 5, 10, 15, 30],
                         'epsilon': [0.01, 0.1, 3, 10, 15, 30],
                         'kernel': ['rbf']},
             pre_dispatch='2*n_jobs', refit=True, return_train_score=False,
             scoring=None, verbose=2)

In [59]:
print('Best params: {}'.format(clf_gs.best_params_))
print('#'*20)
print('Best estimator: {}'.format(clf_gs.best_estimator_))

Best params: {'C': 3, 'epsilon': 10, 'kernel': 'rbf'}
####################
Best estimator: SVR(C=3, cache_size=200, coef0=0.0, degree=3, epsilon=10, gamma='scale',
    kernel='rbf', max_iter=-1, shrinking=True, tol=0.001, verbose=False)


In [60]:
clf_best = clf_gs.best_estimator_.fit(X_train, y_train)
preds_best = clf_gs.predict(X_test)

In [62]:
# Plot 
fig = px.line()

# Only thing I figured is - I could do this 
fig.add_scatter(x=test_dates, y=y_test, mode='lines', name='Real Values CO(GT)')
fig.add_scatter(x=test_dates, y=preds_baseline, mode='lines', name='Predictions CO(GT)')
fig.add_scatter(x=test_dates, y=preds_best, mode='lines', name='Tuned Predictions')

# Show plot 
fig.show();

In [64]:
print('MAE for the best parameters is: {}'.format(mean_absolute_error(y_test, preds_best)))
print('#'*20)
print('MAE increased by {:3.2f}% overall.'.format(
        (mean_absolute_error(y_test, preds_baseline) / mean_absolute_error(y_test, preds_best))))

MAE for the best parameters is: 8.118705192601452
####################
MAE increased by 0.61% overall.


## Plot some more features

In [182]:
# Plot 
fig = px.line()

# Only thing I figured is - I could do this 
fig.add_scatter(x=test_dates, y=y_test, mode='lines', name='Real Values CO(GT)')
fig.add_scatter(x=test_dates, y=preds_best, mode='lines', name='Tuned Predictions',
               fill='tonexty')

# Show plot 
fig.show();

Let's investigate if there a certain times where predictions were better / worse than average. According to the plot above we will say that predictions within the range of `5` are `good`.  The rest is labeled as `not good`.

In [186]:
preds_quality = abs(y_test - preds_best)

In [188]:
labels = []
for x in preds_quality:
    if x <= 5:
        labels.append('Good')
    else:
        labels.append('Bad')

In [190]:
px.scatter(x=test_dates, y=preds_best, color=labels)

Now correlation between time of prediction and quality!